In [16]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `inter2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `inter2incs` : `inter_no` $\mapsto$ `inc_edge_ids`
- `inter2outs` : `inter_no` $\mapsto$ `out_edge_ids`
- `inter2inc2dire` : `inter_no` $\mapsto$ `int2dire`
  - `inc2dire` : `out_edge_id` $\mapsto$ `dire`
- `inter2out2dire` : `inter_no` $\mapsto$ `out2dire`
  - `out2dire` : `inc_edge_id` $\mapsto$ `dire`
- `inter2inc2vec` : `inter_no` $\mapsto$ `int2vec`
  - `inc2vec` : `out_edge_id` $\mapsto$ `vec`
- `inter2out2vec` : `inter_no` $\mapsto$ `out2vec`
  - `out2vec` : `inc_edge_id` $\mapsto$ `vec`

좌회전 판단

Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.

In [17]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
display(self.u_turn)

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


parent_id child_id  adj_inc_edge_id adj_out_edge_id      inc_edge_id  \
0        i0      u00    -571500487_01    571500487_01     571500487_02   
1        i2      u20     571542811_02    571542811_01  571542810_01.51   
2        i3      u30     571556450_02    571556450_01     571556452_01   
3        i3      u31    -571500475_01    571500475_01     571500475_02   
4        i3      u32  571540303_02.21    571540303_01     571540303_02   
5        i6      u60  571500535_02.18    571500535_01     571500535_02   

       out_edge_id  
0  571500487_01.32  
1     571542810_02  
2     571556452_02  
3  571500475_01.26  
4    -571540303_02  
5    -571500535_02

In [11]:
self.u_turn = pd.merge(self.u_turn, self.u_condition, on='child_id')

# p2inc_edge2angle : node_id to inc_edge2angle
p2inc_edge2angle = dict()
# p2out_edge2angle : node_id to out_edge2angle
p2out_edge2angle = dict()
# p2inc_angle2edge : node_id to inc_angle2edge
p2inc_angle2edge = dict()
# p2out_angle2edge : node_id to out_angle2edge
p2out_angle2edge = dict()
for node_id in self.parent_ids:
    m5 = self.match5[self.match5.node_id==node_id]
    m5 = m5.dropna(subset=['inc_edge_id', 'out_edge_id'])
    # inc_edge2angle : inc_edge_id to inc_angle
    inc_edge2angle = dict(zip(m5.inc_edge_id, m5.inc_angle.astype(int)))
    p2inc_edge2angle[node_id] = inc_edge2angle
    # out_edge2angle : out_edge_id to out_angle
    out_edge2angle = dict(zip(m5.out_edge_id, m5.out_angle.astype(int)))
    p2out_edge2angle[node_id] = out_edge2angle
    # inc_angle2edge : inc_angle to inc_edge_id
    inc_angle2edge = dict(zip(m5.inc_angle.astype(int), m5.inc_edge_id))
    p2inc_angle2edge[node_id] = inc_angle2edge
    # out_angle2edge : out_angle to out_edge_id
    out_angle2edge = dict(zip(m5.out_angle.astype(int), m5.out_edge_id))
    p2out_angle2edge[node_id] = out_angle2edge

# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for row in self.u_turn.itertuples():
    parent_id = row.parent_id
    child_id = row.child_id
    condition = row.condition
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    adj_inc_edge_id = row.adj_inc_edge_id
    adj_out_edge_id = row.adj_out_edge_id

    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id

    # 진입엣지 각도
    inc_angle = p2inc_edge2angle[parent_id][adj_inc_edge_id]

    # 이격각도
    self.angle_separation = 10

    # 진입로 각도 목록
    inc_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).inc_angle.astype(int).unique()
    inc_angles = np.sort(inc_angles)
    inc_angles = list(inc_angles - 360) + list(inc_angles) + list(inc_angles + 360)
    inc_angles = np.array(inc_angles)

    # 보행신호시의 진입로 각도
    inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_separation]
    inc_angle_pedes = np.sort(inc_angles_left)[0] % 360

    # 보행신호시의 진입로 엣지id
    inc_angle2edge = p2inc_angle2edge[parent_id]
    inc_edge_id_pedes = inc_angle2edge[inc_angle_pedes]

    # 진출로 각도 목록
    out_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).out_angle.astype(int).unique()
    out_angles = np.sort(out_angles)
    out_angles = list(out_angles - 360) + list(out_angles) + list(out_angles + 360)
    out_angles = np.array(out_angles)

    # 보행신호시의 진입로 각도
    out_angles_right = out_angles[out_angles <= inc_angle - self.angle_separation]
    out_angle_pedes = np.sort(out_angles_right)[-1] % 360

    # 보행신호시의 진입로 엣지id
    out_angle2edge = p2out_angle2edge[parent_id]
    out_edge_id_pedes = out_angle2edge[out_angle_pedes]

    # 진입엣지/진출엣지 포함 조건
    inc_true = (cmatch.inc_edge_id==adj_inc_edge_id)
    out_true = (cmatch.out_edge_id==adj_out_edge_id)

    # 보행신호시 조건
    pedes_flag = (cmatch.inc_edge_id==inc_edge_id_pedes) & (cmatch.out_edge_id==out_edge_id_pedes)

    # 좌회전시 조건
    right_flag = inc_true & (cmatch.turn_type=='left')

    # 보행신호이동류(17) 조건
    crosswalk_on = (cmatch.move_no==17) & ~ out_true

    # 신호없음이동류(18) 조건
    all_redsigns = (cmatch.move_no==18) & ~ out_true

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
    if condition == "보행신호시":
        cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

    uturn_not_assigned = cmatch[['inc_edge_id','out_edge_id']].isna().any(axis=1).all()

    if uturn_not_assigned:
        # 보행신호시
        if pedes_flag.any():
            cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 좌회전시
        elif right_flag.any():
            cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 신호없음이동류(18) 발생시
        elif all_redsigns.any():
            cmatch.loc[all_redsigns, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 진출엣지 미포함시
        elif out_true.any():
            cmatch.loc[~ out_true, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

In [18]:
self.make_match6()
display(self.match6)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

inter_no  move_no inc_dire out_dire       inc_edge_id    out_edge_id  \
0        175        1        동        남      571545870_02   571542797_02   
1        175        2        서        동      571510153_02   571545870_01   
2        175        3        남        서     -571542797_02   571510153_01   
3        175        4        북        남     -571500487_01   571542797_02   
4        175        5        서        북      571510153_02   571500487_01   
..       ...      ...      ...      ...               ...            ...   
60       210       21        북        서  571511538_02.121   571500535_01   
61       210       21        서        남   571500535_02.18   571500585_01   
62       210       21        남        동      571500585_02   571542115_01   
63       210       21        동        북     -571542115_01   571511538_01   
64       210        5        서        북      571500535_02  -571500535_02   

   node_id  
0       i0  
1       i0  
2       i0  
3       i0  
4       i0  
..     ...  
60      i6  
61      i6  
62      i6  
63      i6  
64     u60  

[65 rows x 7 columns]

In [ ]:
self.match6

In [123]:
self.get_intermediates()

2. 중간산출물을 생성합니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.


In [52]:
self.matching[self.matching.node_id=='u60']

inter_no  move_no inc_dire out_dire   inc_edge_id    out_edge_id node_id
64       210        5        서        북  571500535_02  -571500535_02     u60

In [43]:
NODE_ID = 'u00'
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state
print(''.join(self.node2init[NODE_ID]))

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge_id)
        out_edge = self.net.getEdge(out_edge_id)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'
print(''.join(self.node2init[NODE_ID]))

# 유턴교차로
for _, row in self.u_turn.iterrows():
    node_id = row.child_id
    inc_edge_id = row.inc_edge_id
    out_edge = row.out_edge_id
    if not (pd.isna(inc_edge_id) and pd.isna(out_edge_id)):
        inc_edge = self.net.getEdge(inc_edge_id)
        out_edge = self.net.getEdge(out_edge_id)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'
print(''.join(self.node2init[NODE_ID]))



ggggggggg
ggggrgggg
ggggrgggg


In [22]:
self.initialize_state()

self.node2init['u20']

2-2. 비보호우회전(g)을 배정했습니다.


['g', 'g', 'g', 'g', 'g', 'g']

In [131]:
self.node2init['i2']

['r', 'r', 'g', 'g', 'r', 'r', 'r']

In [132]:
self.match6[self.match6.node_id.isin(['i0', 'u00'])]

inter_no node_id  phase_no ring_type  move_no    inc_edge_id  \
0        175      i0         1         A        8  -571542797_02   
1        175      i0         1         B        4  -571500487_01   
2        175      i0         2         A        7  -571500487_01   
3        175      i0         2         B        3  -571542797_02   
4        175      i0         3         A        6   571545870_02   
5        175      i0         3         B        1   571545870_02   
6        175      i0         4         A        5   571510153_02   
7        175      i0         4         B        2   571510153_02   
8        175     u00         1         A        8            NaN   
9        175     u00         1         B        4            NaN   
10       175     u00         2         A        7   571500487_02   
11       175     u00         2         B        3            NaN   
12       175     u00         3         A        6            NaN   
13       175     u00         3         B        1            NaN   
14       175     u00         4         A        5            NaN   
15       175     u00         4         B        2            NaN   

        out_edge_id              state  
0      571500487_01  grrrgrrrgGGGGrgrr  
1      571542797_02  gGGrgrrrgrrrrrgrr  
2      571545870_01  grrGgrrrgrrrrrgrr  
3      571510153_01  grrrgrrrgrrrrGgrr  
4      571510153_01  grrrgGGrgrrrrrgrr  
5      571542797_02  grrrgrrGgrrrrrgrr  
6      571500487_01  grrrgrrrgrrrrrgrG  
7      571545870_01  grrrgrrrgrrrrrgGr  
8               NaN          ggggrgggg  
9               NaN          ggggrgggg  
10  571500487_01.32          ggggGgggg  
11              NaN          ggggrgggg  
12              NaN          ggggrgggg  
13              NaN          ggggrgggg  
14              NaN          ggggrgggg  
15              NaN          ggggrgggg

In [127]:
self.match6[self.match6.node_id.isin(['i2', 'u20'])]

inter_no node_id  phase_no ring_type  move_no      inc_edge_id  \
22       177      i2         1         A        8    -571542809_01   
23       177      i2         1         B        4     571542811_02   
24       177      i2         2         A       17              NaN   
25       177      i2         2         B       18              NaN   
26       177     u20         1         A        8              NaN   
27       177     u20         1         B        4              NaN   
28       177     u20         2         A       17  571542810_01.51   
29       177     u20         2         B       18              NaN   

     out_edge_id    state  
22  571542811_01  rrggGGG  
23  571542809_01  GGggrrr  
24           NaN  rrggrrr  
25           NaN  rrggrrr  
26           NaN   gggggg  
27           NaN   gggggg  
28  571542810_02   ggGggg  
29           NaN   gggggg

In [ ]:
'''Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.'''